In [1]:
import math
import numpy as np
import plotly.express as px
import plotly.graph_objects as go

def parse_tle_file(file_path):

    # Reads TLE data from a local file and parses it.

    try:
        with open(file_path, 'r') as f:
            tle_data = [line.strip() for line in f.readlines()]
    except FileNotFoundError:
        print(f"Error: The file '{file_path}' was not found.")
        return None

    parsed_satellites = []
    for i in range(0, len(tle_data), 3):
        if i + 2 < len(tle_data):
            name = tle_data[i]
            line1 = tle_data[i+1]
            line2 = tle_data[i+2]

            try:
                # Slicing and parsing of data
                satellite_number = int(line1[2:7])
                classification = line1[7]
                international_designator_year = int(line1[9:11])
                international_designator_launch_number = int(line1[11:14])
                international_designator_piece_of_launch = line1[14:17].strip()
                epoch_year = int(line1[18:20])
                epoch_day = float(line1[20:32])
                first_derivative_mean_motion = float(line1[33:43])
                second_derivative_mean_motion = line1[44:52]
                bstar_drag_term = line1[53:61]
                ephemeris_type = int(line1[62])
                element_number = int(line1[64:68])

                inclination = float(line2[8:16])
                raan = float(line2[17:25])
                eccentricity = float("0." + line2[26:33])
                argument_of_perigee = float(line2[34:42])
                mean_anomaly = float(line2[43:51])
                mean_motion = float(line2[52:63])
                revolution_number = int(line2[63:68])

                data = {
                    "name": name,
                    "satellite_number": satellite_number,
                    "classification": classification,
                    "international_designator_year": international_designator_year,
                    "international_designator_launch_number": international_designator_launch_number,
                    "international_designator_piece_of_launch": international_designator_piece_of_launch,
                    "epoch_year": epoch_year,
                    "epoch_day": epoch_day,
                    "first_derivative_mean_motion": first_derivative_mean_motion,
                    "second_derivative_mean_motion": second_derivative_mean_motion,
                    "bstar_drag_term": bstar_drag_term,
                    "ephemeris_type": ephemeris_type,
                    "element_number": element_number,
                    "inclination": inclination,
                    "raan": raan,
                    "eccentricity": eccentricity,
                    "argument_of_perigee": argument_of_perigee,
                    "mean_anomaly": mean_anomaly,
                    "mean_motion": mean_motion,
                    "revolution_number": revolution_number
                }
                parsed_satellites.append(data)
            except (ValueError, IndexError) as e:
                print(f"Skipping malformed TLE entry at index {i} in '{file_path}': {e}")
                continue
    return parsed_satellites

def semi_major_axis(mean_motion):

    # Calculate semi-major axis from mean motion

    G = 6.67430e-11  # Gravitational constant
    M = 5.9722e24    # Earth mass in kg
    n = mean_motion * (2 * math.pi) / (24 * 3600)  # Convert to rad/s
    return (G * M / (n**2)) ** (1/3)

def kepler_to_cartesian(a, e, i, omega, raan, nu):

    # Converts Keplerian orbital elements to Cartesian coordinates.
    # Arguments in radians.

    p = a * (1 - e**2)
    r = p / (1 + e * np.cos(nu))

    x_prime = r * np.cos(nu)
    y_prime = r * np.sin(nu)

    # Rotation matrix to transform from orbital plane to inertial frame
    C11 = np.cos(raan) * np.cos(omega) - np.sin(raan) * np.sin(omega) * np.cos(i)
    C12 = -np.cos(raan) * np.sin(omega) - np.sin(raan) * np.cos(omega) * np.cos(i)
    C21 = np.sin(raan) * np.cos(omega) + np.cos(raan) * np.sin(omega) * np.cos(i)
    C22 = -np.sin(raan) * np.sin(omega) + np.cos(raan) * np.cos(omega) * np.cos(i)
    C31 = np.sin(omega) * np.sin(i)
    C32 = np.cos(omega) * np.sin(i)

    x = C11 * x_prime + C12 * y_prime
    y = C21 * x_prime + C22 * y_prime
    z = C31 * x_prime + C32 * y_prime

    return x, y, z

def plot_interactive_satellite_positions(all_satellites):

    # Creating an interactive 3D plot of satellite positions around Earth

    fig = go.Figure()

    # Plot Earth sphere
    radius_earth = 6371e3  # Earth radius in meters

    # Generate spherical coordinates for Earth
    u = np.linspace(0, 2 * np.pi, 50)
    v = np.linspace(0, np.pi, 25)

    x_earth = radius_earth * np.outer(np.cos(u), np.sin(v))
    y_earth = radius_earth * np.outer(np.sin(u), np.sin(v))
    z_earth = radius_earth * np.outer(np.ones(np.size(u)), np.cos(v))

    # Add Earth as a surface
    fig.add_trace(go.Surface(
        x=x_earth,
        y=y_earth,
        z=z_earth,
        colorscale=[[0, 'darkblue'], [1, 'darkblue']],
        showscale=False,
        opacity=0.6,
        name='Earth',
        hoverinfo='skip'
    ))

    # Prepare data for plotting
    x_coords, y_coords, z_coords = [], [], []
    hover_text = []
    sizes = []

    for data in all_satellites:
        a = data.get("semi_major_axis")
        e = data.get("eccentricity")
        i_rad = np.deg2rad(data.get("inclination"))
        omega_rad = np.deg2rad(data.get("argument_of_perigee"))
        raan_rad = np.deg2rad(data.get("raan"))

        # Use true anomaly of 0 for initial position
        nu_rad = 0

        if a is not None:
            x, y, z = kepler_to_cartesian(a, e, i_rad, omega_rad, raan_rad, np.array([nu_rad]))

            x_coords.append(x[0])
            y_coords.append(y[0])
            z_coords.append(z[0])

            # Adjust marker size based on distance from Earth
            distance = np.sqrt(x[0]**2 + y[0]**2 + z[0]**2)
            size = max(3, min(10, 20 * radius_earth / distance))
            sizes.append(size)

            # Create hover text with satellite data
            text = (f"<b>Name:</b> {data['name']}<br>"
                    f"<b>Satellite ID:</b> {data['satellite_number']}<br>"
                    f"<b>Inclination:</b> {data['inclination']:.2f}°<br>"
                    f"<b>Eccentricity:</b> {data['eccentricity']:.6f}<br>"
                    f"<b>Semi-major Axis:</b> {a/1000:.2f} km<br>"
                    f"<b>Altitude:</b> {(a - radius_earth)/1000:.2f} km")
            hover_text.append(text)

    # Add debris markers
    fig.add_trace(go.Scatter3d(
        x=x_coords,
        y=y_coords,
        z=z_coords,
        mode='markers',
        marker=dict(
            size=sizes,
            color='green',
            opacity=0.9,
            line=dict(width=2, color='darkgreen')
        ),
        text=hover_text,
        hoverinfo='text',
        name='Debris'
    ))

    # Set plot layout and aspect ratio
    max_range = max(max(np.abs(x_coords)), max(np.abs(y_coords)), max(np.abs(z_coords))) if x_coords else 2 * radius_earth

    fig.update_layout(
        title='Debris Positions in Earth Orbit',
        scene=dict(
            xaxis_title='X (meters)',
            yaxis_title='Y (meters)',
            zaxis_title='Z (meters)',
            aspectmode='cube',
            xaxis=dict(range=[-max_range, max_range]),
            yaxis=dict(range=[-max_range, max_range]),
            zaxis=dict(range=[-max_range, max_range])
        ),
        width=1000,
        height=800
    )

    fig.show()

# -Main script execution-
def main():
    # List of TLE files to process
    file_paths = ["2.txt", "4.txt", "5.txt"]
    all_satellites_data = []

    # Parse all TLE files
    for path in file_paths:
        parsed_data = parse_tle_file(path)
        if parsed_data:
            print(f"Successfully parsed {len(parsed_data)} debris TLE entries from '{path}'.")
            all_satellites_data.extend(parsed_data)
        else:
            print(f"Failed to parse data from '{path}'")

    # Calculate orbital parameters for each satellite
    for data in all_satellites_data:
        if "mean_motion" in data:
            try:
                semimajor_axis_m = semi_major_axis(data["mean_motion"])
                data["semi_major_axis"] = semimajor_axis_m
                print(f"Calculated semi-major axis for {data['name']}: {semimajor_axis_m/1000:.2f} km")
            except (ValueError, ZeroDivisionError) as e:
                print(f"Error calculating orbital parameters for {data['name']}: {e}")
                data["semi_major_axis"] = None

    # Display summary
    print(f"\nTotal debris loaded: {len(all_satellites_data)}")

    # Plot all orbits
    if all_satellites_data:
        plot_interactive_satellite_positions(all_satellites_data)
    else:
        print("No debris data to plot.")

if __name__ == "__main__":
    main()

Successfully parsed 1891 debris TLE entries from '2.txt'.
Successfully parsed 606 debris TLE entries from '4.txt'.
Successfully parsed 12549 debris TLE entries from '5.txt'.
Calculated semi-major axis for FENGYUN 1C: 7185.74 km
Calculated semi-major axis for FENGYUN 1C DEB: 7655.09 km
Calculated semi-major axis for FENGYUN 1C DEB: 7676.54 km
Calculated semi-major axis for FENGYUN 1C DEB: 7741.26 km
Calculated semi-major axis for FENGYUN 1C DEB: 7812.25 km
Calculated semi-major axis for FENGYUN 1C DEB: 7778.65 km
Calculated semi-major axis for FENGYUN 1C DEB: 7798.45 km
Calculated semi-major axis for FENGYUN 1C DEB: 8022.86 km
Calculated semi-major axis for FENGYUN 1C DEB: 8056.08 km
Calculated semi-major axis for FENGYUN 1C DEB: 8127.19 km
Calculated semi-major axis for FENGYUN 1C DEB: 7239.15 km
Calculated semi-major axis for FENGYUN 1C DEB: 7191.63 km
Calculated semi-major axis for FENGYUN 1C DEB: 7208.15 km
Calculated semi-major axis for FENGYUN 1C DEB: 7140.44 km
Calculated semi-ma